## Technical Indicators List

All the indicators that https://pypi.org/project/stockstats/ supports

In [23]:
INDICATORS_LIST_ALL = ['high_5_sma','rsi','boll','macd','cr','wr','cci','tr','atr','dma','pdi','dx','adx','adxr','trix','tema','vr','mfi','vwma',
                   'chop','ppo','stochrsi','supertrend','aroon','close_75_z','ao'
                   ]

In [24]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
#%matplotlib inline
import mplfinance as mpf # matplot.finance to plot candlesticks
import random
import itertools # iterators for efficient looping: https://docs.python.org/3/library/itertools.html 

from finrl.meta.preprocessor.yahoodownloader import YahooDownloader # a veces puede dar error al hacer fetch de la data porque no encuentra un stock o sus precios, o por la timezone
from finrl import config_tickers # config_tickers es una clase en la que se guardan en listas los nombres de cada stock para cada índice
from finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from finrl.agents.stablebaselines3.models import DRLAgent
from stable_baselines3.common.logger import configure
from finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline

In [25]:
TRAIN_START_DATE = '2010-01-01'
TRAIN_END_DATE = '2021-10-01'
TEST_START_DATE = '2021-10-01'
TEST_END_DATE = '2023-03-01'

In [26]:
stock = YahooDownloader(start_date = TRAIN_START_DATE,
                     end_date = TEST_END_DATE,
                     ticker_list = config_tickers.DOW_30_TICKER).fetch_data()

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed


[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%******

Shape of DataFrame:  (97013, 8)


In [27]:
stock # this DF contains all the stock price history from the train start date to the test end date, for every firm in the DJ30

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470742  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200787    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090424    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777550    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   
...           ...         ...         ...         ...         ...        ...   
97008  2023-02-28  482.670013  483.359985  473.920013  465.066833    3902100   
97009  2023-02-28  220.000000  221.770004  219.500000  217.824539    5385400   
97010  2023-02-28   38.700001   38.970001   38.549999   35.538387   16685300   
97011  2023-02-28   35.480000   35.779999   35.320000   32.750977    8847000   
97012  2023-02-28   47.000000   47.549999   46.983334   46.346081   18054000   

        tic  day  
0      AAPL    0  
1      AMGN    0  
2       AXP    0  
3        BA    0  
4       CAT    0  
...     ...  ...  
97008   UNH    1  
97009     V    1  
97010    VZ    1  
97011   WBA    1  
97012   WMT    1  

[97013 rows x 8 columns]

In [28]:
stock.day.describe()

count    97013.000000
mean         2.024131
std          1.398530
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max          4.000000
Name: day, dtype: float64

Stock symbols

In [29]:
tickers = stock.tic.unique()

We wanted to get:

In [30]:
print(np.reshape(config_tickers.DOW_30_TICKER, (len(config_tickers.DOW_30_TICKER))))
print("Number of firms in the index: ",len(config_tickers.DOW_30_TICKER))

['AXP' 'AMGN' 'AAPL' 'BA' 'CAT' 'CSCO' 'CVX' 'GS' 'HD' 'HON' 'IBM' 'INTC'
 'JNJ' 'KO' 'JPM' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV' 'UNH' 'CRM'
 'VZ' 'V' 'WBA' 'WMT' 'DIS' 'DOW']
Number of firms in the index:  30


Creo que DOW es el DJIA, la media

But we got (because of the unavailable timezone or price data):

In [31]:
print(tickers) # stocks we have to train the agent
print("Number of firms downloaded: ",len(tickers))

['AAPL' 'AMGN' 'AXP' 'BA' 'CAT' 'CRM' 'CSCO' 'CVX' 'DIS' 'GS' 'HD' 'HON'
 'IBM' 'INTC' 'JNJ' 'JPM' 'KO' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV'
 'UNH' 'V' 'VZ' 'WBA' 'WMT' 'DOW']
Number of firms downloaded:  30


## Agent 4+

with following technical indicators:

In [32]:
# let's first take 6 technical indicators randomly from the supported indicators list
INDICATORS = [INDICATORS_LIST_ALL[i] for i in random.sample(range(len(INDICATORS_LIST_ALL)), 6)]

In [33]:
INDICATORS

['cci', 'supertrend', 'atr', 'trix', 'vwma', 'rsi']

In [34]:
# creamos instancia de FeatureEngineer indicando la configuración deseada para hacer el preproceso
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    tech_indicator_list = INDICATORS,
                    use_vix=True, # AUN NO SE QUE ES ESTO
                    use_turbulence=True, # measures extreme asset price fluctuation --> if the turbulence index reaches a pre-defined threshold, the agent will halt buying action and start selling the holding shares gradually
                    user_defined_feature = False) # MIRA A VER QUÉ ERA DEFINIRSE UNA FEATURE (creo que es )

processed = fe.preprocess_data(stock)

Successfully added technical indicators


[*********************100%%**********************]  1 of 1 completed


Shape of DataFrame:  (3310, 8)
Successfully added vix
Successfully added turbulence index


Comentario: hay indicadores que pese a estar documentados como soportados en https://pypi.org/project/stockstats/, esta versión de código no los reconoce. Habrá que comprobar mediante más pruebas que todos los incluídos en la lista de todos los indicadores, estén soportados por esta versión. 

In [35]:
processed

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470742  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200787    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090424    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777550    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   
...           ...         ...         ...         ...         ...        ...   
95985  2023-02-27  488.769989  490.940002  481.959991  472.278259    3006200   
95986  2023-02-27  220.729996  221.440002  219.339996  218.230591    4255300   
95987  2023-02-27   38.990002   39.150002   38.630001   35.602486   14210900   
95988  2023-02-27   36.049999   36.080002   35.270000   32.621929    5580100   
95989  2023-02-27   47.570000   47.696667   46.886665   46.121090   16647300   

        tic  day         cci  supertrend        atr      trix        vwma  \
0      AAPL    0   66.666667   11.192774   1.189972  0.000000    7.238819   
1      AMGN    0   66.666667  107.222637  16.669212  0.000000   51.876929   
2       AXP    0   66.666667   64.773724   8.009575  0.000000   38.193474   
3        BA    0   66.666667   93.432348  12.612450  0.000000   51.655849   
4       CAT    0   66.666667  115.349335  18.999779  0.000000   52.296739   
...     ...  ...         ...         ...        ...       ...         ...   
95985   UNH    0  -53.478196  528.902606  16.802081 -0.024474  484.963828   
95986     V    0  -85.319415  215.501725   4.173500  0.006921  224.577448   
95987    VZ    0 -105.954167   48.206671   3.680670 -0.120141   38.651600   
95988   WBA    0 -193.255412   42.533680   3.372575 -0.024412   35.301067   
95989   WMT    0  -61.567129   50.711280   1.437521  0.041587   47.647770   

              rsi        vix  turbulence  
0      100.000000  20.040001    0.000000  
1      100.000000  20.040001    0.000000  
2      100.000000  20.040001    0.000000  
3      100.000000  20.040001    0.000000  
4      100.000000  20.040001    0.000000  
...           ...        ...         ...  
95985   44.100885  20.950001    7.163853  
95986   42.108546  20.950001    7.163853  
95987   39.549271  20.950001    7.163853  
95988   42.115760  20.950001    7.163853  
95989   44.050511  20.950001    7.163853  

[95990 rows x 16 columns]

In order to allow the Agent to have a consistent data structure to work with, we need to ensure that each stock has the same data range. This is necessary because not all stocks have data for every trading day due to holidays, stock-specific trading suspensions, or newly listed stocks. Therefore, we will establish a common data interval for each stock with day granularity and fill with 0 the (the more NaNs we have, the worst the performance will be). --> We can check this effect with other Stock Indices with less missing stock prices.

Convert the stock column to list

In [36]:
list_ticker = processed["tic"].unique().tolist()
print(list_ticker)
len(list_ticker)

['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT']


29

Create a list from the minimum to the maximum date and with the same granularity

In [37]:
list_date = list(pd.date_range(processed['date'].min(),processed['date'].max()).astype(str))
list_date

['2010-01-04',
 '2010-01-05',
 '2010-01-06',
 '2010-01-07',
 '2010-01-08',
 '2010-01-09',
 '2010-01-10',
 '2010-01-11',
 '2010-01-12',
 '2010-01-13',
 '2010-01-14',
 '2010-01-15',
 '2010-01-16',
 '2010-01-17',
 '2010-01-18',
 '2010-01-19',
 '2010-01-20',
 '2010-01-21',
 '2010-01-22',
 '2010-01-23',
 '2010-01-24',
 '2010-01-25',
 '2010-01-26',
 '2010-01-27',
 '2010-01-28',
 '2010-01-29',
 '2010-01-30',
 '2010-01-31',
 '2010-02-01',
 '2010-02-02',
 '2010-02-03',
 '2010-02-04',
 '2010-02-05',
 '2010-02-06',
 '2010-02-07',
 '2010-02-08',
 '2010-02-09',
 '2010-02-10',
 '2010-02-11',
 '2010-02-12',
 '2010-02-13',
 '2010-02-14',
 '2010-02-15',
 '2010-02-16',
 '2010-02-17',
 '2010-02-18',
 '2010-02-19',
 '2010-02-20',
 '2010-02-21',
 '2010-02-22',
 '2010-02-23',
 '2010-02-24',
 '2010-02-25',
 '2010-02-26',
 '2010-02-27',
 '2010-02-28',
 '2010-03-01',
 '2010-03-02',
 '2010-03-03',
 '2010-03-04',
 '2010-03-05',
 '2010-03-06',
 '2010-03-07',
 '2010-03-08',
 '2010-03-09',
 '2010-03-10',
 '2010-03-

Assign every day to each stock

In [38]:
combination = list(itertools.product(list_date,list_ticker))
combination

[('2010-01-04', 'AAPL'),
 ('2010-01-04', 'AMGN'),
 ('2010-01-04', 'AXP'),
 ('2010-01-04', 'BA'),
 ('2010-01-04', 'CAT'),
 ('2010-01-04', 'CRM'),
 ('2010-01-04', 'CSCO'),
 ('2010-01-04', 'CVX'),
 ('2010-01-04', 'DIS'),
 ('2010-01-04', 'GS'),
 ('2010-01-04', 'HD'),
 ('2010-01-04', 'HON'),
 ('2010-01-04', 'IBM'),
 ('2010-01-04', 'INTC'),
 ('2010-01-04', 'JNJ'),
 ('2010-01-04', 'JPM'),
 ('2010-01-04', 'KO'),
 ('2010-01-04', 'MCD'),
 ('2010-01-04', 'MMM'),
 ('2010-01-04', 'MRK'),
 ('2010-01-04', 'MSFT'),
 ('2010-01-04', 'NKE'),
 ('2010-01-04', 'PG'),
 ('2010-01-04', 'TRV'),
 ('2010-01-04', 'UNH'),
 ('2010-01-04', 'V'),
 ('2010-01-04', 'VZ'),
 ('2010-01-04', 'WBA'),
 ('2010-01-04', 'WMT'),
 ('2010-01-05', 'AAPL'),
 ('2010-01-05', 'AMGN'),
 ('2010-01-05', 'AXP'),
 ('2010-01-05', 'BA'),
 ('2010-01-05', 'CAT'),
 ('2010-01-05', 'CRM'),
 ('2010-01-05', 'CSCO'),
 ('2010-01-05', 'CVX'),
 ('2010-01-05', 'DIS'),
 ('2010-01-05', 'GS'),
 ('2010-01-05', 'HD'),
 ('2010-01-05', 'HON'),
 ('2010-01-05', 'IB

Merge with stock DF (potentially resulting in NaN values)

In [39]:
processed_full = pd.DataFrame(combination,columns=["date","tic"]).merge(processed,on=["date","tic"],how="left")

Remove non-trading days generated with the date range

In [40]:
processed_full = processed_full[processed_full['date'].isin(processed['date'])]

In [41]:
processed_full

date   tic        open        high         low       close  \
0       2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470742   
1       2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200787   
2       2010-01-04   AXP   40.810001   41.099998   40.389999   33.090424   
3       2010-01-04    BA   55.720001   56.389999   54.799999   43.777550   
4       2010-01-04   CAT   57.650002   59.189999   57.509998   40.190220   
...            ...   ...         ...         ...         ...         ...   
139282  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278259   
139283  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
139284  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
139285  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621929   
139286  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

             volume  day         cci  supertrend        atr      trix  \
0       493729600.0  0.0   66.666667   11.192774   1.189972  0.000000   
1         5277400.0  0.0   66.666667  107.222637  16.669212  0.000000   
2         6894300.0  0.0   66.666667   64.773724   8.009575  0.000000   
3         6186700.0  0.0   66.666667   93.432348  12.612450  0.000000   
4         7325600.0  0.0   66.666667  115.349335  18.999779  0.000000   
...             ...  ...         ...         ...        ...       ...   
139282    3006200.0  0.0  -53.478196  528.902606  16.802081 -0.024474   
139283    4255300.0  0.0  -85.319415  215.501725   4.173500  0.006921   
139284   14210900.0  0.0 -105.954167   48.206671   3.680670 -0.120141   
139285    5580100.0  0.0 -193.255412   42.533680   3.372575 -0.024412   
139286   16647300.0  0.0  -61.567129   50.711280   1.437521  0.041587   

              vwma         rsi        vix  turbulence  
0         7.238819  100.000000  20.040001    0.000000  
1        51.876929  100.000000  20.040001    0.000000  
2        38.193474  100.000000  20.040001    0.000000  
3        51.655849  100.000000  20.040001    0.000000  
4        52.296739  100.000000  20.040001    0.000000  
...            ...         ...        ...         ...  
139282  484.963828   44.100885  20.950001    7.163853  
139283  224.577448   42.108546  20.950001    7.163853  
139284   38.651600   39.549271  20.950001    7.163853  
139285   35.301067   42.115760  20.950001    7.163853  
139286   47.647770   44.050511  20.950001    7.163853  

[95990 rows x 16 columns]

In [42]:
len(processed_full.tic.unique())

29

In [43]:
processed_full.info()

<class 'pandas.core.frame.DataFrame'>
Index: 95990 entries, 0 to 139286
Data columns (total 16 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   date        95990 non-null  object 
 1   tic         95990 non-null  object 
 2   open        95990 non-null  float64
 3   high        95990 non-null  float64
 4   low         95990 non-null  float64
 5   close       95990 non-null  float64
 6   volume      95990 non-null  float64
 7   day         95990 non-null  float64
 8   cci         95990 non-null  float64
 9   supertrend  95990 non-null  float64
 10  atr         95990 non-null  float64
 11  trix        95990 non-null  float64
 12  vwma        95990 non-null  float64
 13  rsi         95990 non-null  float64
 14  vix         95990 non-null  float64
 15  turbulence  95990 non-null  float64
dtypes: float64(14), object(2)
memory usage: 12.4+ MB


In [44]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806766  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935161  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654854  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501177  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day           cci    supertrend           atr          trix  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471     15.194646    100.243242     15.139562      0.048224   
std        1.398649    108.466077     71.285033     11.480137      0.254111   
min        0.000000   -445.631586      6.685321      0.334999     -3.469403   
25%        1.000000    -69.821855     51.748247      6.444613     -0.086613   
50%        2.000000     29.905059     81.492279     12.679734      0.061912   
75%        3.000000     98.763937    133.950500     20.544233      0.199097   
max        4.000000    446.592853    555.780705     74.560923      1.917139   

               vwma           rsi           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean      97.229815     53.406475     18.721163     34.943607  
std       72.056235     12.112899      7.269653     43.065957  
min        6.666191      0.000000      9.140000      0.000000  
25%       44.380098     45.052431     13.630000     14.972703  
50%       77.913009     53.644358     16.875000     24.175786  
75%      132.184505     61.998578     21.760000     39.999511  
max      540.258708    100.000000     82.690002    652.617862

In this case, there are no nulls, but if there were we would need to fill them in the following way. 

In [45]:
processed_full = processed_full.sort_values(['date','tic']) # we need to sort bc of the data_split method CHECK SOURCE CODE 

processed_full = processed_full.fillna(0)

In [46]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806766  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935161  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654854  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501177  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day           cci    supertrend           atr          trix  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471     15.194646    100.243242     15.139562      0.048224   
std        1.398649    108.466077     71.285033     11.480137      0.254111   
min        0.000000   -445.631586      6.685321      0.334999     -3.469403   
25%        1.000000    -69.821855     51.748247      6.444613     -0.086613   
50%        2.000000     29.905059     81.492279     12.679734      0.061912   
75%        3.000000     98.763937    133.950500     20.544233      0.199097   
max        4.000000    446.592853    555.780705     74.560923      1.917139   

               vwma           rsi           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean      97.229815     53.406475     18.721163     34.943607  
std       72.056235     12.112899      7.269653     43.065957  
min        6.666191      0.000000      9.140000      0.000000  
25%       44.380098     45.052431     13.630000     14.972703  
50%       77.913009     53.644358     16.875000     24.175786  
75%      132.184505     61.998578     21.760000     39.999511  
max      540.258708    100.000000     82.690002    652.617862

In [47]:
large_value = 1e9

processed_full.replace([np.inf], large_value, inplace=True)

In [48]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806766  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935161  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654854  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501177  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day           cci    supertrend           atr          trix  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471     15.194646    100.243242     15.139562      0.048224   
std        1.398649    108.466077     71.285033     11.480137      0.254111   
min        0.000000   -445.631586      6.685321      0.334999     -3.469403   
25%        1.000000    -69.821855     51.748247      6.444613     -0.086613   
50%        2.000000     29.905059     81.492279     12.679734      0.061912   
75%        3.000000     98.763937    133.950500     20.544233      0.199097   
max        4.000000    446.592853    555.780705     74.560923      1.917139   

               vwma           rsi           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean      97.229815     53.406475     18.721163     34.943607  
std       72.056235     12.112899      7.269653     43.065957  
min        6.666191      0.000000      9.140000      0.000000  
25%       44.380098     45.052431     13.630000     14.972703  
50%       77.913009     53.644358     16.875000     24.175786  
75%      132.184505     61.998578     21.760000     39.999511  
max      540.258708    100.000000     82.690002    652.617862

Split Train and Test datasets

In [49]:
train = data_split(processed_full, TRAIN_START_DATE,TRAIN_END_DATE)
train

date   tic        open        high         low       close  \
0     2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470742   
0     2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200787   
0     2010-01-04   AXP   40.810001   41.099998   40.389999   33.090424   
0     2010-01-04    BA   55.720001   56.389999   54.799999   43.777550   
0     2010-01-04   CAT   57.650002   59.189999   57.509998   40.190220   
...          ...   ...         ...         ...         ...         ...   
2956  2021-09-30   UNH  401.489990  403.489990  390.459991  375.759705   
2956  2021-09-30     V  227.580002  228.789993  222.630005  218.139221   
2956  2021-09-30    VZ   54.500000   54.509998   54.000000   45.622719   
2956  2021-09-30   WBA   48.790001   48.930000   46.919998   40.519115   
2956  2021-09-30   WMT   46.880001   47.243332   46.416668   44.566536   

           volume  day         cci  supertrend        atr      trix  \
0     493729600.0  0.0   66.666667   11.192774   1.189972  0.000000   
0       5277400.0  0.0   66.666667  107.222637  16.669212  0.000000   
0       6894300.0  0.0   66.666667   64.773724   8.009575  0.000000   
0       6186700.0  0.0   66.666667   93.432348  12.612450  0.000000   
0       7325600.0  0.0   66.666667  115.349335  18.999779  0.000000   
...           ...  ...         ...         ...        ...       ...   
2956    3779900.0  3.0 -167.744825  366.259059  19.483181 -0.124240   
2956    7128500.0  3.0   -0.134262  237.458400   6.846644 -0.112169   
2956   18736600.0  3.0 -105.865985   65.550537   8.759088 -0.074151   
2956    6449400.0  3.0 -142.212698   53.897144   7.464084 -0.066341   
2956   22457700.0  3.0 -160.736181   50.712879   2.257056 -0.171316   

            vwma         rsi        vix  turbulence  
0       7.238819  100.000000  20.040001    0.000000  
0      51.876929  100.000000  20.040001    0.000000  
0      38.193474  100.000000  20.040001    0.000000  
0      51.655849  100.000000  20.040001    0.000000  
0      52.296739  100.000000  20.040001    0.000000  
...          ...         ...        ...         ...  
2956  404.511278   30.703002  23.139999   24.927784  
2956  222.888796   42.173389  23.139999   24.927784  
2956   51.552101   39.353590  23.139999   24.927784  
2956   46.584015   39.868150  23.139999   24.927784  
2956   47.146577   26.449495  23.139999   24.927784  

[85753 rows x 16 columns]

In [50]:
len(train.tic.unique())

29

In [51]:
train.tic.unique()

array(['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS',
       'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM',
       'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT'],
      dtype=object)

In [52]:
trade = data_split(processed_full, TEST_START_DATE,TEST_END_DATE)
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653519   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.514023   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278259   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621929   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

         volume  day         cci  supertrend        atr      trix        vwma  \
0    94639600.0  4.0 -115.227225  151.962220   3.649073 -0.187907  144.381631   
0     2629400.0  4.0  -93.700186  178.648671  20.448650 -0.224565  209.435413   
0     3956000.0  4.0   58.058236  152.435856   8.416823  0.218345  165.426149   
0     9113600.0  4.0   88.122967  209.674360   6.210131  0.012743  218.297611   
0     3695500.0  4.0  -59.553964  227.936152  13.201333 -0.304558  192.977391   
..          ...  ...         ...         ...        ...       ...         ...   
352   3006200.0  0.0  -53.478196  528.902606  16.802081 -0.024474  484.963828   
352   4255300.0  0.0  -85.319415  215.501725   4.173500  0.006921  224.577448   
352  14210900.0  0.0 -105.954167   48.206671   3.680670 -0.120141   38.651600   
352   5580100.0  0.0 -193.255412   42.533680   3.372575 -0.024412   35.301067   
352  16647300.0  0.0  -61.567129   50.711280   1.437521  0.041587   47.647770   

           rsi        vix  turbulence  
0    40.222730  21.100000  120.030541  
0    40.764967  21.100000  120.030541  
0    59.631274  21.100000  120.030541  
0    56.844540  21.100000  120.030541  
0    40.248239  21.100000  120.030541  
..         ...        ...         ...  
352  44.100885  20.950001    7.163853  
352  42.108546  20.950001    7.163853  
352  39.549271  20.950001    7.163853  
352  42.115760  20.950001    7.163853  
352  44.050511  20.950001    7.163853  

[10237 rows x 16 columns]

In [53]:
train_length = len(train)
trade_length = len(trade)
print("Number of training samples: ", train_length)
print("Number of testing samples", trade_length)

Number of training samples:  85753
Number of testing samples 10237


In [54]:
train.tail()

date  tic        open        high         low       close  \
2956  2021-09-30  UNH  401.489990  403.489990  390.459991  375.759705   
2956  2021-09-30    V  227.580002  228.789993  222.630005  218.139221   
2956  2021-09-30   VZ   54.500000   54.509998   54.000000   45.622719   
2956  2021-09-30  WBA   48.790001   48.930000   46.919998   40.519115   
2956  2021-09-30  WMT   46.880001   47.243332   46.416668   44.566536   

          volume  day         cci  supertrend        atr      trix  \
2956   3779900.0  3.0 -167.744825  366.259059  19.483181 -0.124240   
2956   7128500.0  3.0   -0.134262  237.458400   6.846644 -0.112169   
2956  18736600.0  3.0 -105.865985   65.550537   8.759088 -0.074151   
2956   6449400.0  3.0 -142.212698   53.897144   7.464084 -0.066341   
2956  22457700.0  3.0 -160.736181   50.712879   2.257056 -0.171316   

            vwma        rsi        vix  turbulence  
2956  404.511278  30.703002  23.139999   24.927784  
2956  222.888796  42.173389  23.139999   24.927784  
2956   51.552101  39.353590  23.139999   24.927784  
2956   46.584015  39.868150  23.139999   24.927784  
2956   47.146577  26.449495  23.139999   24.927784

In [55]:
trade.head()

date   tic        open        high         low       close  \
0  2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653519   
0  2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0  2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0  2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0  2021-10-01   CAT  192.899994  195.869995  191.240005  183.514023   

       volume  day         cci  supertrend        atr      trix        vwma  \
0  94639600.0  4.0 -115.227225  151.962220   3.649073 -0.187907  144.381631   
0   2629400.0  4.0  -93.700186  178.648671  20.448650 -0.224565  209.435413   
0   3956000.0  4.0   58.058236  152.435856   8.416823  0.218345  165.426149   
0   9113600.0  4.0   88.122967  209.674360   6.210131  0.012743  218.297611   
0   3695500.0  4.0  -59.553964  227.936152  13.201333 -0.304558  192.977391   

         rsi   vix  turbulence  
0  40.222730  21.1  120.030541  
0  40.764967  21.1  120.030541  
0  59.631274  21.1  120.030541  
0  56.844540  21.1  120.030541  
0  40.248239  21.1  120.030541

Since we need to set the parameters for the environment functions, we need to compute the stock dimension and state space.

In [56]:
# Number of unique stocks used for the training 
stock_dimension = len(train.tic.unique())
# {balance, close price, shares, N-technical indicators}
# Balance will occupy 1 input node, and it is computed as: balance = balance (t) − amount of money we pay to buy shares + amount of money we receive to sell shares
# We will have N input nodes for the stock prices and N additional input nodes to indicate the current number of shares for each stock --> 2*N
# we will have one node for every technical indicator for every stock --> M indicators * N stocks
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension (Number of different companies in which we want to invest initially): {stock_dimension}, State Space (Number of input nodes to feed to the network): {state_space}")

Stock Dimension (Number of different companies in which we want to invest initially): 29, State Space (Number of input nodes to feed to the network): 233


Most of the trading companies demand trading commissions or costs. Here, we will simulate a buying and selling commission of 0,1% for each transaction. We will assume the user starts having no shares of any stock. Let's also assume we have 1.000.000 dollars to invest with. We will also define a parameter that sets the maximum amount of shares to trade, h_max. It is interesting to set the scaling reward or gamma (importance we give to the future reward), so that we specify if we give more importance to the short or long term. We could modify these parameters, if needed.

In [57]:
buy_cost_list = sell_cost_list = [0.001] * stock_dimension
num_stock_shares = [0] * stock_dimension
h_max = 100
initial_amount = 1000000
gamma = 1e-4 # we are assuming we want to get the highest return in the short term, preventing ourselves from the risk and uncertainty caused by external factors in the long term

HAZ PRUEBAS CON UN GAMMA MÁS ALTO

Let's set the configuration that will be passed to the Environment class

In [58]:
env_kwargs = {
    "hmax": h_max,
    "initial_amount": initial_amount, 
    "num_stock_shares": num_stock_shares,
    "buy_cost_pct": buy_cost_list,
    "sell_cost_pct": sell_cost_list,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": gamma
}

Let's create the Stock Trading Environment!

In [59]:
e_train_gym = StockTradingEnv(df = train, **env_kwargs) # creates instance of the Environment class
print("Environment class type", type(e_train_gym))
env_train, _ = e_train_gym.get_sb_env() # resets the environment and converts the initial environment into a DummyVecEnv instance
print("External Environment class type: ", type(env_train))

Environment class type <class 'finrl.meta.env_stock_trading.env_stocktrading.StockTradingEnv'>
External Environment class type:  <class 'stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv'>


Since we will use different RL algorithms, let's set some flags:

In [60]:
if_using_a2c = True
if_using_ddpg = True
if_using_ppo = True
if_using_td3 = True
if_using_sac = True

Let's create the Deep Reinforcement Learning Agent!

podríamos runear todos los ind (p.e. 3 o 4 ind) y con los mejores, cambiar el resto de parametros (fechas, gamma,...)

# A2C

In [64]:
agent = DRLAgent(env = env_train) # creates Agent instance
model_a2c = agent.get_model("a2c") # gets stablebaselines3 model  

if if_using_a2c: # where to store the results
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_4+' + '/a2c'
  new_logger_a2c = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_a2c.set_logger(new_logger_a2c)

{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device
Logging to resultadosTFG/set_4+/a2c


Let's train the agent!

In [65]:
trained_a2c = agent.train_model(model=model_a2c, 
                             tb_log_name='a2c',
                             total_timesteps=50000) if if_using_a2c else None

--------------------------------------
| time/                 |            |
|    fps                | 171        |
|    iterations         | 100        |
|    time_elapsed       | 2          |
|    total_timesteps    | 500        |
| train/                |            |
|    entropy_loss       | -41.4      |
|    explained_variance | -0.21      |
|    learning_rate      | 0.0007     |
|    n_updates          | 99         |
|    policy_loss        | 7.64       |
|    reward             | 0.06787415 |
|    std                | 1.01       |
|    value_loss         | 1.23       |
--------------------------------------
--------------------------------------
| time/                 |            |
|    fps                | 175        |
|    iterations         | 200        |
|    time_elapsed       | 5          |
|    total_timesteps    | 1000       |
| train/                |            |
|    entropy_loss       | -41.3      |
|    explained_variance | -0.434     |
|    learning_rate      |

In [66]:
trained_a2c.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [67]:
learning_process = pd.read_csv("resultadosTFG/set_4+/a2c/progress.csv")
learning_process

train/value_loss  time/total_timesteps  train/policy_loss  \
0           1.231411                   500           7.637074   
1           3.049834                  1000         -28.079792   
2           2.632887                  1500         -14.625578   
3          16.044987                  2000         115.847580   
4          54.005432                  2500        -296.739990   
..               ...                   ...                ...   
95          0.691010                 48000          12.023348   
96          0.961520                 48500           7.958418   
97         27.167088                 49000        -221.372894   
98          2.464178                 49500         -32.181072   
99         60.570007                 50000         268.451355   

    train/entropy_loss  train/reward  train/n_updates  train/learning_rate  \
0           -41.352562      0.067874               99               0.0007   
1           -41.316898      0.764009              199               0.0007   
2           -41.372845     -3.366277              299               0.0007   
3           -41.322632      1.271992              399               0.0007   
4           -41.326805     -0.731704              499               0.0007   
..                 ...           ...              ...                  ...   
95          -42.481464     -1.487989             9599               0.0007   
96          -42.512062     -1.194672             9699               0.0007   
97          -42.553684      0.617221             9799               0.0007   
98          -42.494083      1.145026             9899               0.0007   
99          -42.521202    -11.020602             9999               0.0007   

    time/iterations  train/explained_variance  train/std  time/time_elapsed  \
0               100             -2.100106e-01   1.007124                  2   
1               200             -4.336870e-01   1.006009                  5   
2               300              2.479017e-03   1.007978                  8   
3               400              0.000000e+00   1.006138                 11   
4               500              0.000000e+00   1.006367                 14   
..              ...                       ...        ...                ...   
95             9600              0.000000e+00   1.050232                320   
96             9700              0.000000e+00   1.051260                324   
97             9800              0.000000e+00   1.052764                328   
98             9900             -1.192093e-07   1.050860                331   
99            10000             -1.192093e-07   1.051902                334   

    time/fps  
0        171  
1        175  
2        177  
3        173  
4        173  
..       ...  
95       149  
96       149  
97       149  
98       149  
99       149  

[100 rows x 12 columns]

Plot the training results

In [68]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    # List of tuples containing (y-axis, title)
    metrics = [
        ('train/reward', 'Reward'),
        ('train/policy_loss', 'Policy Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/n_updates', 'Number of Updates'),
        ('train/value_loss', 'Value Loss'),
        ('time/fps', 'Frames Per Second'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_4+/a2c/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=2)  # Modify n_rows and n_cols as needed


The agent is not learning very well... 

Podríamos hacer una tabla resumen de todos los algos y pones cuántos steps han sido necesarios, la LR de cada uno, etc

# PPO

Set PPO parameters and set the logger

In [69]:
agent = DRLAgent(env = env_train)
PPO_PARAMS = {
    "n_steps": 2048,
    "ent_coef": 0.01,
    "learning_rate": 0.00025,
    "batch_size": 128,
}
model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

if if_using_ppo:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_4+' + '/ppo'
  new_logger_ppo = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ppo.set_logger(new_logger_ppo)

{'n_steps': 2048, 'ent_coef': 0.01, 'learning_rate': 0.00025, 'batch_size': 128}
Using cpu device
Logging to resultadosTFG/set_4+/ppo


Train PPO

In [70]:
trained_ppo = agent.train_model(model=model_ppo, 
                             tb_log_name='ppo',
                             total_timesteps=50000) if if_using_ppo else None

-----------------------------------
| time/              |            |
|    fps             | 185        |
|    iterations      | 1          |
|    time_elapsed    | 11         |
|    total_timesteps | 2048       |
| train/             |            |
|    reward          | 0.54575825 |
-----------------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 189         |
|    iterations           | 2           |
|    time_elapsed         | 21          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.013253635 |
|    clip_fraction        | 0.182       |
|    clip_range           | 0.2         |
|    entropy_loss         | -41.2       |
|    explained_variance   | -0.0302     |
|    learning_rate        | 0.00025     |
|    loss                 | 2.71        |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.027      |
|   

In [71]:
trained_ppo.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [72]:
learning_process = pd.read_csv("resultadosTFG/set_4+/ppo/progress.csv")
learning_process

time/iterations  time/time_elapsed  time/total_timesteps  time/fps  \
0                 1                 11                  2048       185   
1                 2                 21                  4096       189   
2                 3                 32                  6144       190   
3                 4                 42                  8192       193   
4                 5                 52                 10240       194   
5                 6                 62                 12288       195   
6                 7                 72                 14336       196   
7                 8                 83                 16384       196   
8                 9                 93                 18432       196   
9                10                104                 20480       196   
10               11                114                 22528       197   
11               12                124                 24576       197   
12               13                134                 26624       197   
13               14                144                 28672       197   
14               15                155                 30720       198   
15               16                165                 32768       198   
16               17                176                 34816       196   
17               18                187                 36864       196   
18               19                199                 38912       195   
19               20                209                 40960       195   
20               21                219                 43008       195   
21               22                230                 45056       195   
22               23                240                 47104       195   
23               24                250                 49152       196   
24               25                260                 51200       196   

    train/reward  train/value_loss  train/policy_gradient_loss  \
0       0.545758               NaN                         NaN   
1      -0.189997          9.773271                   -0.026951   
2       2.116505         44.017469                   -0.017656   
3       0.877870         72.498078                   -0.018522   
4      -1.423428         19.538700                   -0.018968   
5      -0.056811         51.355001                   -0.022986   
6       2.396220        135.386826                   -0.014720   
7      -2.111330         27.366164                   -0.018364   
8       0.763790         83.327531                   -0.025261   
9      -2.333292        117.334656                   -0.015162   
10     -1.026568        135.450363                   -0.017431   
11      1.105936         32.968220                   -0.024489   
12     -0.099868        277.405733                   -0.016813   
13      6.877479        157.351249                   -0.015630   
14      0.797522         26.677917                   -0.018746   
15      0.641011        179.455427                   -0.014812   
16     -3.551092        263.980478                   -0.016596   
17     -3.626664         56.866249                   -0.019733   
18      0.160370        183.741750                   -0.015549   
19     -0.657604         75.539335                   -0.014598   
20     -0.545485         34.472132                   -0.020554   
21      0.567799         96.018577                   -0.014936   
22      0.139381        113.463613                   -0.013237   
23     -0.738756         70.180735                   -0.011036   
24      1.739994         24.206125                   -0.028737   

    train/entropy_loss  train/learning_rate  train/explained_variance  \
0                  NaN                  NaN                       NaN   
1           -41.196694              0.00025                 -0.030198   
2           -41.265865              0.00025                 -0.014098   
3           -41.306043              0.00025                 -0.007928 

Plot the training results

In [73]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()

    metrics = [
        ('train/reward', 'Reward'),
        ('train/loss', 'Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/approx_kl', 'approximate Kullback-Leibler divergence'),
        ('train/clip_fraction', 'Clip Fraction'),
        ('train/clip_range', 'Clip Range'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/value_loss', 'Value Loss'),
        ('train/policy_gradient_loss', 'Policy Gradient Loss'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_4+/ppo/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=2)  # Modify n_rows and n_cols as needed

# DDPG

Create the agent and set the logger

In [74]:
agent = DRLAgent(env = env_train)
model_ddpg = agent.get_model("ddpg")

if if_using_ddpg:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_4+' + '/ddpg'
  new_logger_ddpg = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ddpg.set_logger(new_logger_ddpg)

{'batch_size': 128, 'buffer_size': 50000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_4+/ddpg


Train the agent

In [75]:
trained_ddpg = agent.train_model(model=model_ddpg, 
                             tb_log_name='ddpg',
                             total_timesteps=50000) if if_using_ddpg else None

day: 2956, episode: 40
begin_total_asset: 1000000.00
end_total_asset: 6619431.99
total_reward: 5619431.99
total_cost: 7984.11
total_trades: 33351
Sharpe: 0.954
-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 99         |
|    time_elapsed    | 118        |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | 77.6       |
|    critic_loss     | 9.85e+03   |
|    learning_rate   | 0.001      |
|    n_updates       | 8871       |
|    reward          | -6.8344936 |
-----------------------------------
-----------------------------------
| time/              |            |
|    episodes        | 8          |
|    fps             | 91         |
|    time_elapsed    | 258        |
|    total_timesteps | 23656      |
| train/             |            |
|    actor_loss      | 10.9       |
|    critic_loss     | 47         |
|    learning_rate   | 0.001      |
|    n_updat

In [76]:
trained_ddpg.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_

Let's see the learning progress of the agent 

In [77]:
learning_process = pd.read_csv("resultadosTFG/set_4+/ddpg/progress.csv")
learning_process

train/critic_loss  train/actor_loss  time/total_timesteps  train/reward  \
0        9853.598628         77.598906                 11828     -6.834494   
1          46.976459         10.930211                 23656     -6.834494   
2          11.279857          2.007890                 35484     -6.834494   
3           4.975373         -2.865798                 47312     -6.834494   

   train/n_updates  train/learning_rate  time/time_elapsed  time/episodes  \
0             8871                0.001                118              4   
1            20699                0.001                258              8   
2            32527                0.001                403             12   
3            44355                0.001                551             16   

   time/fps  
0        99  
1        91  
2        87  
3        85

Plot the results of the training

In [78]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_4+/ddpg/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# TD3

Create the agent and set the logger

In [79]:
agent = DRLAgent(env = env_train)
TD3_PARAMS = {"batch_size": 100, 
              "buffer_size": 1000000, 
              "learning_rate": 0.001}

model_td3 = agent.get_model("td3",model_kwargs = TD3_PARAMS)

if if_using_td3:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_4+' + '/td3'
  new_logger_td3 = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_td3.set_logger(new_logger_td3)

{'batch_size': 100, 'buffer_size': 1000000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_4+/td3


/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/stable_baselines3/common/buffers.py:241: UserWarning: This system does not have apparently enough memory to store the complete replay buffer 1.99GB > 1.19GB
  warnings.warn(


Train TD3

In [80]:
trained_td3 = agent.train_model(model=model_td3, 
                             tb_log_name='td3',
                             total_timesteps=50000) if if_using_td3 else None

day: 2956, episode: 60
begin_total_asset: 1000000.00
end_total_asset: 6312802.54
total_reward: 5312802.54
total_cost: 1128.08
total_trades: 35504
Sharpe: 0.943
-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 98         |
|    time_elapsed    | 119        |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | 88.4       |
|    critic_loss     | 1.26e+03   |
|    learning_rate   | 0.001      |
|    n_updates       | 8871       |
|    reward          | -12.133539 |
-----------------------------------
-----------------------------------
| time/              |            |
|    episodes        | 8          |
|    fps             | 91         |
|    time_elapsed    | 257        |
|    total_timesteps | 23656      |
| train/             |            |
|    actor_loss      | 54.1       |
|    critic_loss     | 568        |
|    learning_rate   | 0.001      |
|    n_updat

In [81]:
trained_td3.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_

Let's see agent's learning process

In [82]:
learning_process = pd.read_csv("resultadosTFG/set_4+/td3/progress.csv")
learning_process

train/critic_loss  train/actor_loss  time/total_timesteps  train/reward  \
0        1259.568594         88.435164                 11828    -12.133539   
1         568.095509         54.051722                 23656    -12.133539   
2         132.579332         50.203559                 35484    -12.133539   
3          28.925231         55.430906                 47312    -12.133539   

   train/n_updates  train/learning_rate  time/time_elapsed  time/episodes  \
0             8871                0.001                119              4   
1            20699                0.001                257              8   
2            32527                0.001                408             12   
3            44355                0.001                561             16   

   time/fps  
0        98  
1        91  
2        86  
3        84

Plot training results

In [83]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_4+/td3/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# SAC

Create the agent, set parameters for training, and set logger

In [84]:
agent = DRLAgent(env = env_train)
SAC_PARAMS = {
    "batch_size": 128,
    "buffer_size": 100000,
    "learning_rate": 0.0001,
    "learning_starts": 100,
    "ent_coef": "auto_0.1",
}

model_sac = agent.get_model("sac",model_kwargs = SAC_PARAMS)

if if_using_sac:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_4+' + '/sac'
  new_logger_sac = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_sac.set_logger(new_logger_sac)

{'batch_size': 128, 'buffer_size': 100000, 'learning_rate': 0.0001, 'learning_starts': 100, 'ent_coef': 'auto_0.1'}
Using cpu device
Logging to resultadosTFG/set_4+/sac


Train SAC

In [85]:
trained_sac = agent.train_model(model=model_sac, 
                             tb_log_name='sac',
                             total_timesteps=50000) if if_using_sac else None

-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 49         |
|    time_elapsed    | 236        |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | 1.89e+03   |
|    critic_loss     | 8.33e+03   |
|    ent_coef        | 0.286      |
|    ent_coef_loss   | 136        |
|    learning_rate   | 0.0001     |
|    n_updates       | 11727      |
|    reward          | -4.6851115 |
-----------------------------------
day: 2956, episode: 80
begin_total_asset: 1000000.00
end_total_asset: 4025736.20
total_reward: 3025736.20
total_cost: 284026.11
total_trades: 72049
Sharpe: 0.724
-----------------------------------
| time/              |            |
|    episodes        | 8          |
|    fps             | 47         |
|    time_elapsed    | 493        |
|    total_timesteps | 23656      |
| train/             |            |
|    actor_loss      | 1.05e+03   |
|    criti

In [86]:
trained_sac.policy

SACPolicy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (latent_pi): Sequential(
      (0): Linear(in_features=233, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
    )
    (mu): Linear(in_features=256, out_features=29, bias=True)
    (log_std): Linear(in_features=256, out_features=29, bias=True)
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
      (4): Linear(in_features=256, out_features=1, bias=True)
    )
    (qf1): Sequential(
      (0): Linear(in_features=262, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=2

Let's see agent's learning process

In [87]:
learning_process = pd.read_csv("resultadosTFG/set_4+/sac/progress.csv")
learning_process

train/critic_loss  train/actor_loss  time/total_timesteps  train/reward  \
0        8325.181641       1892.915649                 11828     -4.685111   
1         135.863693       1050.139038                 23656    -16.582344   
2          71.921768        512.463623                 35484    -12.448790   
3          16.882208        282.240509                 47312    -11.993078   

   train/n_updates  train/learning_rate  time/time_elapsed  time/episodes  \
0            11727               0.0001                236              4   
1            23555               0.0001                493              8   
2            35383               0.0001                695             12   
3            47211               0.0001                873             16   

   time/fps  train/ent_coef  train/ent_coef_loss  
0        49        0.285932           136.328369  
1        47        0.125603           -91.066917  
2        51        0.039469          -108.623619  
3        54        0.012466          -110.649788

Agent's training results

In [88]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/ent_coef_loss', 'Entropy coefficient Loss'),
        ('train/ent_coef', 'Entropy coefficient'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_4+/sac/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=1)  # Modify n_rows and n_cols as needed

# Testing

There is a new environment for testing

We feed the environment with the testing dataset we prepared before (from start test date to end test date: with closing prices, etc)

In [89]:
e_trade_gym = StockTradingEnv(df = trade, turbulence_threshold = 70,risk_indicator_col='vix', **env_kwargs)
e_trade_gym

Environment from Stable baselines3; observations is a matrix containing the inputs {balance, close price, shares, N-technical indicators}

In [90]:
env_trade, obs_trade = e_trade_gym.get_sb_env()
env_trade

In [91]:
obs_trade

array([[ 1.00000000e+06,  1.40653519e+02,  1.95822235e+02,
         1.67727463e+02,  2.26000000e+02,  1.83514023e+02,
         2.74900909e+02,  5.07116699e+01,  9.38071136e+01,
         1.75438217e+02,  3.52330658e+02,  3.07771057e+02,
         2.03622498e+02,  1.20424355e+02,  5.01258278e+01,
         1.48433212e+02,  1.54524475e+02,  4.87658386e+01,
         2.28277786e+02,  1.26340294e+02,  7.50690994e+01,
         2.82857452e+02,  1.42315781e+02,  1.30338379e+02,
         1.43675705e+02,  3.77384949e+02,  2.25689667e+02,
         4.58676796e+01,  4.03038139e+01,  4.38215256e+01,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+0

In [92]:
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653519   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.514023   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278259   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621929   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

         volume  day         cci  supertrend        atr      trix        vwma  \
0    94639600.0  4.0 -115.227225  151.962220   3.649073 -0.187907  144.381631   
0     2629400.0  4.0  -93.700186  178.648671  20.448650 -0.224565  209.435413   
0     3956000.0  4.0   58.058236  152.435856   8.416823  0.218345  165.426149   
0     9113600.0  4.0   88.122967  209.674360   6.210131  0.012743  218.297611   
0     3695500.0  4.0  -59.553964  227.936152  13.201333 -0.304558  192.977391   
..          ...  ...         ...         ...        ...       ...         ...   
352   3006200.0  0.0  -53.478196  528.902606  16.802081 -0.024474  484.963828   
352   4255300.0  0.0  -85.319415  215.501725   4.173500  0.006921  224.577448   
352  14210900.0  0.0 -105.954167   48.206671   3.680670 -0.120141   38.651600   
352   5580100.0  0.0 -193.255412   42.533680   3.372575 -0.024412   35.301067   
352  16647300.0  0.0  -61.567129   50.711280   1.437521  0.041587   47.647770   

           rsi        vix  turbulence  
0    40.222730  21.100000  120.030541  
0    40.764967  21.100000  120.030541  
0    59.631274  21.100000  120.030541  
0    56.844540  21.100000  120.030541  
0    40.248239  21.100000  120.030541  
..         ...        ...         ...  
352  44.100885  20.950001    7.163853  
352  42.108546  20.950001    7.163853  
352  39.549271  20.950001    7.163853  
352  42.115760  20.950001    7.163853  
352  44.050511  20.950001    7.163853  

[10237 rows x 16 columns]

## A2C

Test, predict

In [93]:
trained_model = trained_a2c
df_account_value_a2c, df_actions_a2c = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653519e+02  1.95822235e+02  1.67727463e+02
   2.26000000e+02  1.83514023e+02  2.74900909e+02  5.07116699e+01
   9.38071136e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622498e+02  1.20424355e+02  5.01258278e+01  1.48433212e+02
   1.54524475e+02  4.87658386e+01  2.28277786e+02  1.26340294e+02
   7.50690994e+01  2.82857452e+02  1.42315781e+02  1.30338379e+02
   1.43675705e+02  3.77384949e+02  2.25689667e+02  4.58676796e+01
   4.03038139e+01  4.38215256e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Plot and Save testing results, Portfolio Value

In [94]:
df_account_value_a2c['date'] = pd.to_datetime(df_account_value_a2c['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_a2c['date'], df_account_value_a2c['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for A2C')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_4+/a2c/testing/accountValue.png')
plt.close()

Trades made in testing

In [95]:
display(df_actions_a2c)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01    61   100   79  30  100   28   100   55    0   0  ...  100    90   
2021-10-04    61   100   79  30  100   28   100   55    0   0  ...  100    90   
2021-10-05    61   100   79  30  100   28   100   55    0   0  ...  100    90   
2021-10-06    61   100   79  30  100   28   100   55    0   0  ...  100    90   
2021-10-07    61   100   79  30  100   28   100   55    0   0  ...  100    90   
...          ...   ...  ...  ..  ...  ...   ...  ...  ...  ..  ...  ...   ...   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH   V  VZ  WBA  WMT  
date                                             
2021-10-01    0  70    0    0  20  67    0   27  
2021-10-04    0  70    0    0  20  67    0   27  
2021-10-05    0  70    0    0  20  67    0   27  
2021-10-06    0  70    0    0  20  67    0   27  
2021-10-07    0  70    0    0  20  67    0   27  
...         ...  ..  ...  ...  ..  ..  ...  ...  
2023-02-17    0   0    0    0   0   0    0    0  
2023-02-21    0   0    0    0   0   0    0    0  
2023-02-22    0   0    0    0   0   0    0    0  
2023-02-23    0   0    0    0   0   0    0    0  
2023-02-24    0   0    0    0   0   0    0    0  

[352 rows x 29 columns]

## PPO

Test, predict

In [96]:
trained_model = trained_ppo
df_account_value_ppo, df_actions_ppo = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653519e+02  1.95822235e+02  1.67727463e+02
   2.26000000e+02  1.83514023e+02  2.74900909e+02  5.07116699e+01
   9.38071136e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622498e+02  1.20424355e+02  5.01258278e+01  1.48433212e+02
   1.54524475e+02  4.87658386e+01  2.28277786e+02  1.26340294e+02
   7.50690994e+01  2.82857452e+02  1.42315781e+02  1.30338379e+02
   1.43675705e+02  3.77384949e+02  2.25689667e+02  4.58676796e+01
   4.03038139e+01  4.38215256e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Save Plot of Portfolio Value

In [97]:
df_account_value_ppo['date'] = pd.to_datetime(df_account_value_ppo['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ppo['date'], df_account_value_ppo['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for PPO')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_4+/ppo/testing/accountValue.png')
plt.close()


Trades made in testing

In [98]:
df_actions_ppo.tail(40)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2022-12-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-06     0     0    1   0    0   -1     0    0    0   0  ...    0     0   
2023-01-09     0     0    1   0    0   -1     0    0    0   0  ...    0     0   
2023-01-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-11     0     0    2   0    0   -2     0    0    0   0  ...    0     0   
2023-01-12     0     0    1   0    0   -2     0    0    0   0  ...    0     0   
2023-01-13     0     0    2   0    0   -2     0    0    0   0  ...    0     0   
2023-01-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-19     0     0    6  -2    0   -3     0    0    0   0  ...    0     0   
2023-01-20     0     0    3   0   -1   -2     0    0    0   0  ...    0     0   
2023-01-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-26     0     0    1   0    0   -1     0    0    0   0  ...    0     0   
2023-01-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-31     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-07     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-16     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2022-12-28    0   0    0    0  0   0    0    0  
2022-12-29    0   0    0    0  0   0    0    0  
2022-12-30    0   0    0    0  0   0    0    0  
2023-01-03    0   0    0    0  0   0    0    0  
2023-01-04    0   0    0    0  0   0    0    0  
2023-01-05    0   0    0    0  0   0    0    0  
2023-01-06    0   0    0    0  0   0    0    0  
2023-01-09    0   0    0    0  0   0    0    0  
2023-01-10    0   0    0    0  0   0    0    0  
2023-01-11    0   0    0    0  0   0    0    0  
2023-01-12    0   0  

## DDPG

Test DDPG, predict

In [99]:
trained_model = trained_ddpg
df_account_value_ddpg, df_actions_ddpg = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653519e+02  1.95822235e+02  1.67727463e+02
   2.26000000e+02  1.83514023e+02  2.74900909e+02  5.07116699e+01
   9.38071136e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622498e+02  1.20424355e+02  5.01258278e+01  1.48433212e+02
   1.54524475e+02  4.87658386e+01  2.28277786e+02  1.26340294e+02
   7.50690994e+01  2.82857452e+02  1.42315781e+02  1.30338379e+02
   1.43675705e+02  3.77384949e+02  2.25689667e+02  4.58676796e+01
   4.03038139e+01  4.38215256e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [100]:
df_account_value_ddpg['date'] = pd.to_datetime(df_account_value_ddpg['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ddpg['date'], df_account_value_ddpg['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for DDPG')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_4+/ddpg/testing/accountValue.png')
plt.close()


Trades made in testing

In [101]:
df_actions_ddpg.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                            ...        
2021-10-01     0   100    0   0  100    0   100  100    0  100  ...    0   
2021-10-04     0   100    0   0  100    0   100  100    0  100  ...    0   
2021-10-05     0   100    0   0  100    0   100  100    0  100  ...    0   
2021-10-06     0   100    0   0  100    0   100  100    0  100  ...    0   
2021-10-07     0     0    0   0  100    0   100  100    0  100  ...    0   
2021-10-08     0     0    0   0    0    0     0    1    0    0  ...    0   
2021-10-11     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-12     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-13     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-14     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-15     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-18     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-19     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0   0    0    0     0    0    0    0  ...    0   

            MSFT  NKE   PG  TRV  UNH    V  VZ  WBA  WMT  
date                                                     
2021-10-01   100  100  100    0    0  100   0  100    0  
2021-10-04   100  100  100    0    0  100   0  100    0  
2021-10-05   100  100  100    0    0  100   0  100    0  
2021-10-06   100  100  100    0    0  100   0  100    0  
2021-10-07    26    0    0    0    0    0   0  100    0  
2021-10-08     0    0    0    0    0    0   0    0    0  
2021-10-11     0    0    0    0    0    0   0    0    0  
2021-10-12     0    0    0    0    0    0   0    0    0  
2021-10-13     0    0    0    0    0    0   0    0    0  
2021-10-14     0    0    0    0    0    0   0    0    0  
2021-10-15     0    0    0    0    0    0   0    0    0  
2021-10-18     0    0    0    0    0    0   0    0    0  
2021-10-19     0    0    0    0    0    0   0    0    0  
2021-10-20     0    0    0    0    0    0   0    0    0  
2021-10-21     0    0    0    0    0    0   0    0    0  
2021-10-22     0    0    0    0    0    0   0    0    0  
2021-10-25     0    0    0    0    0    0   0    0    0  
2021-10-26     0    0    0    0    0    0   0    0    0  
2021-10-27     0    0    0    0    0    0   0    0    0  
2021-10-28     0    0    0    0    0    0   0    0    0  
2021-10-29     0    0    0    0    0    0   0    0    0  
2021-11-01     0    0    0    0    0    0   0    0    0  
2021-11-02     0    0    0    0    0    0   0    0    0  
2021-11-03     0    0    0    0    0    0   0    0    0  
2021-11-04     0    0    0    0    0    0   0    0    0  
2021-11-05   

## TD3

Test TD3, predict

In [102]:
trained_model = trained_td3
df_account_value_td3, df_actions_td3 = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653519e+02  1.95822235e+02  1.67727463e+02
   2.26000000e+02  1.83514023e+02  2.74900909e+02  5.07116699e+01
   9.38071136e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622498e+02  1.20424355e+02  5.01258278e+01  1.48433212e+02
   1.54524475e+02  4.87658386e+01  2.28277786e+02  1.26340294e+02
   7.50690994e+01  2.82857452e+02  1.42315781e+02  1.30338379e+02
   1.43675705e+02  3.77384949e+02  2.25689667e+02  4.58676796e+01
   4.03038139e+01  4.38215256e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [103]:
df_account_value_td3['date'] = pd.to_datetime(df_account_value_td3['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_td3['date'], df_account_value_td3['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for TD3')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_4+/td3/testing/accountValue.png')
plt.close()


Trades made in testing

In [104]:
df_actions_td3.head(30)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  \
date                                                            ...        
2021-10-01     0   100    0  100    0    0     0    0  100   0  ...  100   
2021-10-04     0   100    0  100    0    0     0    0  100   0  ...  100   
2021-10-05     0   100    0  100    0    0     0    0  100   0  ...  100   
2021-10-06     0   100    0  100    0    0     0    0  100   0  ...  100   
2021-10-07     0     8    0  100    0    0     0    0  100   0  ...  100   
2021-10-08     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-11     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-12     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-13     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-14     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-15     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-18     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-19     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-20     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-21     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-22     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-25     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-26     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-27     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-28     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-29     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-01     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-02     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-03     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-04     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-05     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-08     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-09     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-10     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-11     0     0    0    0    0    0     0    0    0   0  ...    0   

            MSFT  NKE  PG  TRV  UNH    V  VZ  WBA  WMT  
date                                                    
2021-10-01     0    0   0    0  100  100   0  100  100  
2021-10-04     0    0   0    0  100  100   0  100  100  
2021-10-05     0    0   0    0  100  100   0  100  100  
2021-10-06     0    0   0    0  100  100   0  100  100  
2021-10-07     0    0   0    0  100  100   0  100  100  
2021-10-08     0    0   0    0    0 -100   0    0  100  
2021-10-11     0    0   0    0    0 -100   0    0  100  
2021-10-12     0    0   0    0    0 -100   0    0  100  
2021-10-13     0    0   0    0    0 -100   0    1  100  
2021-10-14     0    0   0    0    0 -100   0    0  100  
2021-10-15     0    0   0    0    0    0   0    0    0  
2021-10-18     0    0   0    0    0    0   0    0    0  
2021-10-19     0    0   0    0    0    0   0    0    0  
2021-10-20     0    0   0    0    0    0   0    0    0  
2021-10-21     0    0   0    0    0    0   0    0    0  
2021-10-22     0    0   0    0    0    0   0    0    0  
2021-10-25     0    0   0    0    0    0   0    0    0  
2021-10-26     0    0   0    0    0    0   0    0    0  
2021-10-27     0    0   0    0    0    0   0    0    0  
2021-10-28     0    0   0    0    0    0   0    0    0  
2021-10-29     0    0   0    0    0    0   0    0    0  
2021-11-01     0    0   0    0    0    0   0    0    0  
2021-11-02     0    0   0    0    0    0   0    0    0  
2021-11-03     0    0   0    0    0    0   0    0    0  
2021-11-04     0    0   0    0    0    0   0    0    0  
2021-11-05     0    0   0    0    0    0

## SAC

Test SAC, predict

Account value is the DF that stores the history of the value of the assets (portfolio value)

In [105]:
trained_model = trained_sac
df_account_value_sac, df_actions_sac = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653519e+02  1.95822235e+02  1.67727463e+02
   2.26000000e+02  1.83514023e+02  2.74900909e+02  5.07116699e+01
   9.38071136e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622498e+02  1.20424355e+02  5.01258278e+01  1.48433212e+02
   1.54524475e+02  4.87658386e+01  2.28277786e+02  1.26340294e+02
   7.50690994e+01  2.82857452e+02  1.42315781e+02  1.30338379e+02
   1.43675705e+02  3.77384949e+02  2.25689667e+02  4.58676796e+01
   4.03038139e+01  4.38215256e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [106]:
df_account_value_sac['date'] = pd.to_datetime(df_account_value_sac['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_sac['date'], df_account_value_sac['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for SAC')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_4+/sac/testing/accountValue.png')
plt.close()


Trades made in testing

In [107]:
df_actions_sac.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01     0    94    0   0    0   94    86   69    0   0  ...   53    73   
2021-10-04     0    94    0   0    0   94    86   69    0   0  ...   53    73   
2021-10-05     0    94    0   0    0   94    86   69    0   0  ...   53    73   
2021-10-06     0    94    0   0    0   94    86   69    0   0  ...   53    73   
2021-10-07     0    94    0   0    0   94    86   69    0   0  ...   53    73   
2021-10-08     0    94    0   0    0   94    86    0    0   0  ...    0     0   
2021-10-11     0     0    0   0    0    0     0    0    0   0  ...    0    95   
2021-10-12     0     0    0   0    0    0     0    0    0   0  ...    0    99   
2021-10-13     0     0    0   0    0    0     0    0    0   0  ...   68    99   
2021-10-14     0     0    0   0    0    0   -56    0    0   0  ...    1    99   
2021-10-15     0     0    0   0    0    0   -90  -23    0   0  ...   99    42   
2021-10-18     0     0    0   0    0    0   -90    0    0   0  ...   99     0   
2021-10-19     0     0    0   0    0    0   -95    0    0   0  ...    1    18   
2021-10-20     0     0    0   0    0    0   -91  -20    0   0  ...   99    48   
2021-10-21     0     0    0   0    0    0   -38    0    0   0  ...    0    21   
2021-10-22     0     0    0   0    0    2   -14    0    0   0  ...    0     0   
2021-10-25     0     0    0   0    0    0   -22    0    0   0  ...    1     0   
2021-10-26     0     0    0   0    0    0    -8   -5    0   0  ...    1     0   
2021-10-27     0     0    0   0    0    0    -2    0    0   0  ...    1     0   
2021-10-28     0     0    0   0    0    0     0  -10    0   0  ...    1     0   
2021-10-29     0     0    0   0    0    0   -10   -4    0   0  ...    0     0   
2021-11-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-02     0     0    0   0    0    0     0  -35    0   0  ...    0     0   
2021-11-03     0     0    0   0    0    0     0  -42    0   0  ...    0     0   
2021-11-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-09     0     0    0   0    0    0     0    0    0   0  ...    1     0   
2021-11-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2021-10-01    0  52    0   56  0  80    0   57  
2021-10-04    0  52    0   56  0  80    0   57  
2021-10-05    0  52    0   56  0  80    0   57  
2021-10-06    0  52    0   56  0  80    0   57  
2021-10-07    0  52    0   56  0  80    0   57  
2021-10-08    0   0    0    0  0   0    0    1  
2021-10-11    0  99   99  -41  0   0    0  -99  
2021-10-12    0  99   99  -26  0   0    0  -99  
2021-10-13    0  99    0   -6  0  99    0  -88  
2021-10-14    0  99    0    0  0   0    0    0  
2021-10-15    0  99    1    0  0   1    0    0  
2021-10-18    0  91    0    0  0   1    0    0  
2021-10-19    0  99    0    0  0 -27    0    0  
2021-10-20    0  99    0    0  0 -34    0    0  
2021-10-21    0  99    0   -9  0   0    0    0  
2021-10-22    0   1    0    0  0   0    0    0  
2021-10-25    0  37    0   -9  0   1    0    0  
2021-10-26    0  32    0   -8  0   1    0    0  
2021-10-27    0  49    0  -15  0   0    0    0  
2021-10-28    0  82    0  -23  0   0    0    0  
2021-10-29    0  86    0  -24  0   0    0    0  
2021-11-01    0  91    0  -28  0   0    0    0  
2021-11-02    0  52    0   -8  0   0    0    0  
2021-11-03    0  31    0    0  0   1    0    0  
2021-11-04    0   0    0    0  0   0    0    0  
2021-11-05    0   0    0    0  0   0    0    0  
2021-11-08    0   0    0    0  0   0    0    0 

Obtain results to then merge: merge in one DF the Portfolio Value given by each algorithm

In [108]:
df_result_a2c = df_account_value_a2c.set_index(df_account_value_a2c.columns[0])
df_result_a2c.rename(columns = {'account_value':'a2c'}, inplace = True)
df_result_ddpg = df_account_value_ddpg.set_index(df_account_value_ddpg.columns[0])
df_result_ddpg.rename(columns = {'account_value':'ddpg'}, inplace = True)
df_result_td3 = df_account_value_td3.set_index(df_account_value_td3.columns[0])
df_result_td3.rename(columns = {'account_value':'td3'}, inplace = True)
df_result_ppo = df_account_value_ppo.set_index(df_account_value_ppo.columns[0])
df_result_ppo.rename(columns = {'account_value':'ppo'}, inplace = True)
df_result_sac = df_account_value_sac.set_index(df_account_value_sac.columns[0])
df_result_sac.rename(columns = {'account_value':'sac'}, inplace = True)

We can also get stats from each stock individually (even though the analysis won't focus on that)

In [109]:
#baseline stats

print("==============Get Baseline Stats===========")
print("==============Baseline Stats of Profitability from DJIA===========")
print("This is the real performance of the index")
df_dji_ = get_baseline(
        ticker="^DJI", 
        start = TEST_START_DATE,
        end = TEST_END_DATE)
stats = backtest_stats(df_dji_, value_col_name = 'close')

==============Get Baseline Stats===========
==============Baseline Stats of Profitability from DJIA===========
This is the real performance of the index


[*********************100%%**********************]  1 of 1 completed

Shape of DataFrame:  (354, 8)
Annual return         -0.034876
Cumulative returns    -0.048644
Annual volatility      0.181612
Sharpe ratio          -0.105351
Calmar ratio          -0.158953
Stability              0.280983
Max drawdown          -0.219408
Omega ratio            0.982546
Sortino ratio         -0.146974
Skew                        NaN
Kurtosis                    NaN
Tail ratio             0.970602
Daily value at risk   -0.022957
dtype: float64


get_baseline vuelve a fetchear los stocks de YahooFinance dadas esas fechas.

backtest_stats llama a get daily return y luego saca stats de esa Serie con metodo que pide:

    """
    Calculates various performance metrics of a strategy, for use in
    plotting.show_perf_stats.

    Parameters
    ----------
    returns : pd.Series
        Daily returns of the strategy, noncumulative.
         - See full explanation in tears.create_full_tear_sheet.
    factor_returns : pd.Series, optional
        Daily noncumulative returns of the benchmark factor to which betas are
        computed. Usually a benchmark such as market returns.
         - This is in the same style as returns.
         - If None, do not compute alpha, beta, and information ratio.
    positions : pd.DataFrame
        Daily net position values.
         - See full explanation in tears.create_full_tear_sheet.
    transactions : pd.DataFrame
        Prices and amounts of executed trades. One row per trade.
        - See full explanation in tears.create_full_tear_sheet.
    turnover_denom : str
        Either AGB or portfolio_value, default AGB.
        - See full explanation in txn.get_turnover.

    Returns
    -------
    pd.Series
        Performance metrics.
    """

get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it

In [110]:
df_dji = pd.DataFrame()
df_dji['date'] = df_account_value_a2c['date']
df_dji['account_value'] = df_dji_['close'] / df_dji_['close'][0] * env_kwargs["initial_amount"] # get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it
#df_dji.to_csv("df_dji.csv")
df_dji = df_dji.set_index(df_dji.columns[0])
#df_dji.to_csv("df_dji+.csv")

In [111]:
df_dji.rename(columns = {'account_value':'dji'}, inplace = True)

In [112]:
df_result_td3

td3
date                    
2021-10-01  1.000000e+06
2021-10-04  9.976078e+05
2021-10-05  1.000271e+06
2021-10-06  1.001338e+06
2021-10-07  1.012606e+06
...                  ...
2023-02-21  9.818070e+05
2023-02-22  9.780137e+05
2023-02-23  9.842763e+05
2023-02-24  9.702630e+05
2023-02-27  9.706789e+05

[353 rows x 1 columns]

Compare DJIA with the rest of the algorithms

In [113]:
result = pd.DataFrame()
result = pd.merge(result, df_result_a2c, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ddpg, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_td3, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ppo, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_sac, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_dji, how='outer', left_index=True, right_index=True)
display(result)

a2c          ddpg           td3           ppo  \
date                                                                 
2021-10-01  1.000000e+06  1.000000e+06  1.000000e+06  1.000000e+06   
2021-10-04  9.984252e+05  9.974476e+05  9.976078e+05  9.994588e+05   
2021-10-05  1.000346e+06  1.002202e+06  1.000271e+06  9.999620e+05   
2021-10-06  1.001479e+06  1.003977e+06  1.001338e+06  1.000375e+06   
2021-10-07  1.006204e+06  1.011556e+06  1.012606e+06  1.001432e+06   
...                  ...           ...           ...           ...   
2023-02-21  1.090243e+06  9.933997e+05  9.818070e+05  9.237639e+05   
2023-02-22  1.085879e+06  9.885813e+05  9.780137e+05  9.220253e+05   
2023-02-23  1.089647e+06  9.934396e+05  9.842763e+05  9.265035e+05   
2023-02-24  1.074934e+06  9.859582e+05  9.702630e+05  9.090546e+05   
2023-02-27  1.079680e+06  9.904055e+05  9.706789e+05  9.141644e+05   

                     sac           dji  
date                                    
2021-10-01  1.000000e+06  1.000000e+06  
2021-10-04  9.979529e+05  9.905746e+05  
2021-10-05  1.000699e+06  9.996566e+05  
2021-10-06  1.002556e+06  1.002637e+06  
2021-10-07  1.008913e+06  1.012483e+06  
...                  ...           ...  
2023-02-21  9.274800e+05  9.651327e+05  
2023-02-22  9.274681e+05  9.626710e+05  
2023-02-23  9.315511e+05  9.658412e+05  
2023-02-24  9.202721e+05  9.560240e+05  
2023-02-27  9.219827e+05  9.581264e+05  

[353 rows x 6 columns]

Save and Plot!

In [114]:
plt.rcParams["figure.figsize"] = (15,5)
plt.figure();
result.plot();
plt.savefig(f'resultadosTFG/set_4+/AlgorithmsVsDJI.png')
plt.close()